### Importing Libraries

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from sklearn.model_selection import train_test_split, GridSearchCV
import spacy
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.svm import SVC
from sklearn.metrics import accuracy_score
import warnings
warnings.filterwarnings('ignore')
from sklearn.ensemble import GradientBoostingClassifier
import sys
import xgboost as xgb
import lightgbm as lgb
import nltk
from nltk.sentiment import SentimentIntensityAnalyzer
nltk.download('vader_lexicon')

sia = SentimentIntensityAnalyzer()


2023-12-14 19:49:09.999701: I tensorflow/core/util/port.cc:113] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2023-12-14 19:49:10.042923: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2023-12-14 19:49:10.042947: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2023-12-14 19:49:10.044208: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2023-12-14 19:49:10.051298: I tensorflow/core/platform/cpu_feature_guar

In [2]:
%load_ext autoreload
%autoreload 1
%aimport twitter_disaster_classification

**Load data**

In [3]:
training_data = pd.read_csv('/home/utk.edu/nnaraya2/phase2/CS_522/Final_Project/train.csv', index_col='id')
print('The shape of the training data is ', training_data.shape)
training_data.head(3)

The shape of the training data is  (7613, 4)


keyword location                                               text  target
id                                                                            
1      NaN      NaN  Our Deeds are the Reason of this #earthquake M...       1
4      NaN      NaN             Forest fire near La Ronge Sask. Canada       1
5      NaN      NaN  All residents asked to 'shelter in place' are ...       1

In [4]:
training_data = training_data.drop(['keyword','location'],axis = 1)
training_data.head(3)

text  target
id                                                           
1   Our Deeds are the Reason of this #earthquake M...       1
4              Forest fire near La Ronge Sask. Canada       1
5   All residents asked to 'shelter in place' are ...       1

**Bert embeddings**

In [5]:
from transformers import BertTokenizer, BertModel
import torch

def get_bert_embeddings(text):
    # Load pre-trained model tokenizer and model
    tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
    model = BertModel.from_pretrained('bert-base-uncased')

    # Encode the text and add [CLS] and [SEP] tokens
    input_ids = tokenizer.encode(text, add_special_tokens=True)
    input_tensor = torch.tensor([input_ids])

    # Get the embeddings
    with torch.no_grad():
        outputs = model(input_tensor)
        # The last hidden-state is the first element of the output tuple
        last_hidden_states = outputs.last_hidden_state

    return last_hidden_states.squeeze()

# Example usage
text = "Hello, this is a BERT embedding example."
embeddings = get_bert_embeddings(text)
print(embeddings)


Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


tensor([[-0.2458, -0.3870, -0.2746,  ..., -0.6783,  0.0161,  0.7708],
        [-0.0540, -0.4230,  0.1120,  ..., -0.3561,  0.5633,  0.3239],
        [-0.4821, -0.1938, -0.0772,  ..., -0.6728,  0.0163,  0.5351],
        ...,
        [-0.4737,  0.2784, -0.7968,  ..., -0.4551, -0.5010,  0.3612],
        [ 0.6544,  0.1218, -0.7294,  ...,  0.2810, -0.6138, -0.3577],
        [ 0.4075,  0.1664, -0.5314,  ...,  0.5007, -0.8272, -0.2734]])


In [6]:
# Generate BERT embeddings for each text
bert_embeddings = training_data['text'].apply(lambda x: get_bert_embeddings(x))

# Convert the embeddings into a DataFrame
embedding_data = pd.DataFrame(bert_embeddings.tolist(), index=training_data.index)

# Concatenate the original data with the embeddings
training_data = pd.concat([training_data, embedding_data], axis=1)

# Drop the columns that are not needed
training_data.drop(['text'], axis=1, inplace=True)

# Display the DataFrame
print('Done')

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.predictions.decoder.weight', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertModel: ['cls.predictions.decoder.weight', 'cls.seq_relationsh

Done


In [7]:
training_data

target                                                  0
id                                                              
1           1  [[tensor(-0.1258), tensor(0.4258), tensor(0.19...
4           1  [[tensor(-0.9437), tensor(-0.1667), tensor(-0....
5           1  [[tensor(-0.5628), tensor(-0.7380), tensor(0.4...
6           1  [[tensor(-0.5254), tensor(0.0877), tensor(-0.1...
7           1  [[tensor(-0.1980), tensor(-0.0294), tensor(0.2...
...       ...                                                ...
10869       1  [[tensor(0.0355), tensor(0.0214), tensor(-0.09...
10870       1  [[tensor(0.0816), tensor(0.0395), tensor(-0.06...
10871       1  [[tensor(-0.3473), tensor(-0.0693), tensor(0.1...
10872       1  [[tensor(-0.4801), tensor(-0.3781), tensor(0.0...
10873       1  [[tensor(-0.1205), tensor(-0.4491), tensor(0.2...

[7613 rows x 2 columns]